<a href="https://colab.research.google.com/github/gautambhowmick/cryptocurrency-project/blob/master/reinforcement_learning.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# CryptoCoin Speculator - Data Driven Exploration

- How do CryptoCoin markets behave?

- What causes sudden spikes and dips in cryptocurrency values?

- Are different altcoins, such as Litecoin and Ripple, correlated or independent?

- How to predict what will happen next?

### Outline

- Retrieve, analyze, and visualize different cryptocurrencies.

- Discover interesting trends in how these volatile markets behave.

- How are they evolving.

- Where and how to fetch the Data and explore them.

# Setup and Data Fetch

- Import the required dependencies.

- Import Plotly and enable the offline mode.

- Setup Quandl API and get an API key.

- Define a function to download and cache datasets from Quandl.

- Use pickle to serialize and save downloaded data as a file, avoid re-downloading the same data.

- The function will return the data as a Pandas dataframe. These are spreadsheets on steroids!

In [0]:
#!ls -al

In [0]:
!pip install --upgrade plotly

    100% |████████████████████████████████| 35.7MB 1.0MB/s 
  Found existing installation: plotly 3.6.1
    Uninstalling plotly-3.6.1:
      Successfully uninstalled plotly-3.6.1


In [0]:
!pip install quandl

  Stored in directory: /root/.cache/pip/wheels/9f/5a/d3/6fc3bf6516d2a3eb7e18f9f28b472110b59325f3f258fe9211
Successfully built inflection


In [0]:
import os
import numpy as np
import pandas as pd
import pickle
import quandl
from datetime import datetime

In [0]:
# configure plotly
def configure_plotly_browser_state():
  import IPython
  display(IPython.core.display.HTML('''
        <script src="/static/components/requirejs/require.js"></script>
        <script>
          requirejs.config({
            paths: {
              base: '/static/base',
              plotly: 'https://cdn.plot.ly/plotly-1.5.1.min.js?noext',
            },
          });
        </script>
        '''))

configure_plotly_browser_state()

In [0]:
import plotly 
plotly.tools.set_credentials_file(username='gautam_bhowmick', api_key='sNtJ5zmTpdMel8LiN2I7')
import plotly.offline as py
import plotly.graph_objs as go
import plotly.figure_factory as ff
py.init_notebook_mode(connected=True)

In [0]:
quandl.ApiConfig.api_key = "J3BnsCRV4D89YiT5aXav"

In [0]:
def get_quandl_data(quandl_id):
    '''Download and cache Quandl dataseries'''
    
    cache_path = '{}.pkl'.format(quandl_id).replace('/','-')
    try:
        f = open(cache_path, 'rb')
        df = pickle.load(f)   
        print('Loaded {} from cache'.format(quandl_id))
    except (OSError, IOError) as e:
        print('Downloading {} from Quandl'.format(quandl_id))
        df = quandl.get(quandl_id, returns="pandas")
        df.to_pickle(cache_path)
        print('Cached {} at {}'.format(quandl_id, cache_path))
    return df

# Kraken

- Historical Bitcoin exchange rate from the Kraken Bitcoin exchange.
- Inspect the first 5 rows of the dataframe using the head() method.
- Visually verify that the data looks correct.

# Visualization
- Plotly is used for visualizations. Produces fully-interactive charts using D3.js. 
- These charts have attractive visual defaults, are easy to explore, and are very simple to embed in web pages.

- Compare the generated chart with publically Bitcoin prices(e.g. Coinbase)

In [0]:
# Pull Kraken BTC price exchange data
btc_usd_price_kraken = get_quandl_data('BCHARTS/KRAKENUSD')

Cached BCHARTS/KRAKENUSD at BCHARTS-KRAKENUSD.pkl


In [0]:
btc_usd_price_kraken.head()

Open       High        Low      Close  Volume (BTC)  \
Date                                                                   
2014-01-07  874.67040  892.06753  810.00000  810.00000     15.622378   
2014-01-08  810.00000  899.84281  788.00000  824.98287     19.182756   
2014-01-09  825.56345  870.00000  807.42084  841.86934      8.158335   
2014-01-10  839.99000  857.34056  817.00000  857.33056      8.024510   
2014-01-11  858.20000  918.05471  857.16554  899.84105     18.748285   

            Volume (Currency)  Weighted Price  
Date                                           
2014-01-07       13151.472844      841.835522  
2014-01-08       16097.329584      839.156269  
2014-01-09        6784.249982      831.572913  
2014-01-10        6780.220188      844.938794  
2014-01-11       16698.566929      890.671709

In [0]:
# NOTE: need to call configure_plotly_browser_state() in every cell that we need to plot
configure_plotly_browser_state()
# Chart the BTC pricing data
btc_trace = go.Scatter(x=btc_usd_price_kraken.index, y=btc_usd_price_kraken['Weighted Price'])
py.iplot([btc_trace])

# Other Exchanges
- Pull Pricing Data from various BTC Exchanges.   There is a reason!
- Kraken has a glitch in dataset - few notable down-spikes, late 2014 and early 2016. 
- Distributed nature of Bitcoin exchanges means no single exchange contains a true "master price" of Bitcoin. 
- Pull data from three major exchanges and calculate an aggregate Bitcoin price index.

- Download the data from each exchange into a dictionary of dataframes.
- Merge All Of The Pricing Data Into A Single Dataframe. "Weighted Price" columns
- Preview and verify last five rows the result using the tail() method
- Visualize The Pricing Datasets to compare. 

In [0]:
# Pull pricing data for 3 more BTC exchanges
exchanges = ['COINBASE','BITSTAMP','ITBIT']

exchange_data = {}

exchange_data['KRAKEN'] = btc_usd_price_kraken

for exchange in exchanges:
    exchange_code = 'BCHARTS/{}USD'.format(exchange)
    btc_exchange_df = get_quandl_data(exchange_code)
    exchange_data[exchange] = btc_exchange_df

Cached BCHARTS/COINBASEUSD at BCHARTS-COINBASEUSD.pkl
Cached BCHARTS/BITSTAMPUSD at BCHARTS-BITSTAMPUSD.pkl
Cached BCHARTS/ITBITUSD at BCHARTS-ITBITUSD.pkl


In [0]:
btc_usd_price_coinbase=exchange_data['COINBASE']
btc_usd_price_coinbase.head()

Open    High     Low   Close  Volume (BTC)  Volume (Currency)  \
Date                                                                          
2015-02-04  228.77  230.25  221.85  227.11   3344.120783       7.578076e+05   
2015-05-11  241.59  245.49  239.50  242.86   6176.481242       1.498052e+06   
2015-05-12  242.74  243.40  240.37  242.03   6322.571412       1.531046e+06   
2015-05-13  242.04  244.13  235.54  236.32  10028.946883       2.424123e+06   
2015-05-14  236.93  240.00  232.61  237.46  10365.968041       2.462002e+06   

            Weighted Price  
Date                        
2015-02-04      226.608934  
2015-05-11      242.541273  
2015-05-12      242.155569  
2015-05-13      241.712609  
2015-05-14      237.508205

In [0]:
# NOTE: need to call configure_plotly_browser_state() in every cell that we need to plot
configure_plotly_browser_state()
# Chart the BTC pricing data
btc_trace = go.Scatter(x=btc_usd_price_coinbase.index, y=btc_usd_price_coinbase['Weighted Price'])
py.iplot([btc_trace])

In [0]:
btc_usd_price_bitstamp=exchange_data['BITSTAMP']
btc_usd_price_bitstamp.head()

Open  High   Low  Close  Volume (BTC)  Volume (Currency)  \
Date                                                                   
2011-09-13  5.80  6.00  5.65   5.97     58.371382         346.097389   
2011-09-14  5.58  5.72  5.52   5.53     61.145984         341.854813   
2011-09-15  5.12  5.24  5.00   5.13     80.140795         408.259002   
2011-09-16  4.82  4.87  4.80   4.85     39.914007         193.763147   
2011-09-17  4.87  4.87  4.87   4.87      0.300000           1.461000   

            Weighted Price  
Date                        
2011-09-13        5.929231  
2011-09-14        5.590798  
2011-09-15        5.094272  
2011-09-16        4.854515  
2011-09-17        4.870000

In [0]:
# NOTE: need to call configure_plotly_browser_state() in every cell that we need to plot
configure_plotly_browser_state()
# Chart the BTC pricing data
btc_trace = go.Scatter(x=btc_usd_price_bitstamp.index, y=btc_usd_price_bitstamp['Weighted Price'])
py.iplot([btc_trace])

In [0]:
btc_usd_price_itbit=exchange_data['ITBIT']
btc_usd_price_itbit.head()

Open    High     Low   Close  Volume (BTC)  Volume (Currency)  \
Date                                                                          
2013-08-25  109.22  111.40  109.22  111.40           2.0             220.62   
2013-08-26  105.83  105.83  105.83  105.83           1.0             105.83   
2013-08-27    0.00    0.00    0.00    0.00           0.0               0.00   
2013-08-28    0.00    0.00    0.00    0.00           0.0               0.00   
2013-08-29    0.00    0.00    0.00    0.00           0.0               0.00   

            Weighted Price  
Date                        
2013-08-25          110.31  
2013-08-26          105.83  
2013-08-27            0.00  
2013-08-28            0.00  
2013-08-29            0.00

In [0]:
# NOTE: need to call configure_plotly_browser_state() in every cell that we need to plot
configure_plotly_browser_state()
# Chart the BTC pricing data
btc_trace = go.Scatter(x=btc_usd_price_itbit.index, y=btc_usd_price_itbit['Weighted Price'])
py.iplot([btc_trace])

In [0]:
def merge_dfs_on_column(dataframes, labels, col):
    '''Merge a single column of each dataframe into a new combined dataframe'''
    series_dict = {}
    for index in range(len(dataframes)):
        series_dict[labels[index]] = dataframes[index][col]
        
    return pd.DataFrame(series_dict)

In [0]:
# Merge the BTC price dataseries' into a single dataframe
btc_usd_datasets = merge_dfs_on_column(list(exchange_data.values()), list(exchange_data.keys()), 'Weighted Price')
btc_usd_datasets=btc_usd_datasets.fillna(value=0.00)

In [0]:
btc_usd_datasets.head()

BITSTAMP  COINBASE  ITBIT  KRAKEN
Date                                         
2011-09-13  5.929231       0.0    0.0     0.0
2011-09-14  5.590798       0.0    0.0     0.0
2011-09-15  5.094272       0.0    0.0     0.0
2011-09-16  4.854515       0.0    0.0     0.0
2011-09-17  4.870000       0.0    0.0     0.0

# Verify

The prices look to be as expected: they are in similar ranges, but with slight variations based on the supply and demand of each individual Bitcoin exchange.

# Visualize

- View how these pricing datasets compare. 
- Define a helper function to provide a single-line command to generate a graph from the dataframe.

In [0]:
def df_scatter(df, title, seperate_y_axis=False, x_axis_label='',y_axis_label='', scale='linear', initial_hide=False):
    '''Generate a scatter plot of the entire dataframe'''
    label_arr = list(df)
    series_arr = list(map(lambda col: df[col], label_arr))
  
    y_axis_config = dict(
        overlaying='y',
        showticklabels=False,
        type=scale )
    
    visibility = 'visible'
    if initial_hide:
        visibility = 'legendonly'
        
    # Form Trace For Each Series
    trace_arr = []
    for index, series in enumerate(series_arr):
        trace = go.Scatter(
            x=series.index, 
            y=series, 
            name=label_arr[index]  #,  visible=visibility
        )
        
        # Add seperate axis for the series
        if seperate_y_axis:
            trace['yaxis'] = 'y{}'.format(index + 1)
            layout['yaxis{}'.format(index + 1)] = y_axis_config    
        trace_arr.append(trace)
        
    layout = go.Layout(
        title=title,
        legend=dict(orientation="h"),
        xaxis=dict(title=x_axis_label, type='date'),
        yaxis=dict(title=y_axis_label, showticklabels= not seperate_y_axis,type=scale)
    )
    
    fig = go.Figure(data=trace_arr, layout=layout)
    py.iplot(fig)

In [0]:
# NOTE: need to call configure_plotly_browser_state() in every cell that we need to plot
configure_plotly_browser_state()
# Plot all of the BTC exchange prices
df_scatter(btc_usd_datasets,'Bitcoin Price (USD) By Exchange',False,'Year','USD','linear',False)

# Clean and Aggregate Pricing 
- Remove all zero values from the dataframe


In [0]:
#Remove "0" values
#btc_usd_datasets.replace(0, np.nan, inplace=True)

# Compute Average
New column, containing the daily average Bitcoin price across all of the exchanges.

In [0]:
# Calculate the average BTC price as a new column
btc_usd_datasets['AVGBTCPRICEUSD'] = btc_usd_datasets.mean(axis=1)

In [0]:
# NOTE: need to call configure_plotly_browser_state() in every cell that we need to plot
import cufflinks as cf
configure_plotly_browser_state()
# Plot the average BTC price
btc_trace = go.Scatter(x=btc_usd_datasets.index, y=btc_usd_datasets['AVGBTCPRICEUSD'])
py.iplot([btc_trace])

# AltCoins

- Retrieve Altcoin Pricing Data
- The non-Bitcoin cryptocurrencies are commonly referred to as altcoins.

- Define Poloniex API Helper Functions
- Define two helper functions to download and cache JSON data from this API. 
- get_json_data, which will download and cache JSON data from a provided URL.
- Format Poloniex API HTTP requests and call  get_json_data function to save the resulting data.

- Download Trading Data From Poloniex
- * Most altcoins cannot be bought directly with USD; to acquire these coins individuals often buy Bitcoins and then trade the Bitcoins for altcoins on cryptocurrency exchanges. *

- Download the exchange rate to BTC for each coin, and then use existing BTC pricing to convert this value to USD.

- We'll download exchange data for nine of the top cryptocurrencies 
-- Ethereum
-- Litecoin
-- Ripple
-- Ethereum Classic
-- Stellar
-- Dashcoin
-- Siacoin
-- Monero
-- NEM
-- DigiByte
-- Grin
-- Theta
-- Neblio

- Now we have a dictionary of 13 dataframes, each containing the historical daily average exchange prices between the altcoin and Bitcoin. We can preview the last few rows of the Ethereum price table to make sure it looks ok.

In [0]:
def get_json_data(json_url, cache_path):
    '''Download and cache JSON data, return as a dataframe.'''
    try:        
        f = open(cache_path, 'rb')
        df = pickle.load(f)   
        print('Loaded {} from cache'.format(json_url))
    except (OSError, IOError) as e:
        print('Downloading {}'.format(json_url))
        df = pd.read_json(json_url)
        df.to_pickle(cache_path)
        print('Cached response at {}'.format(json_url, cache_path))
    return df

In [0]:
base_polo_url = 'https://poloniex.com/public?command=returnChartData&currencyPair={}&start={}&end={}&period={}'
start_date = datetime.strptime('2015-01-01', '%Y-%m-%d') # get data from the start of 2015
end_date = datetime.now() # up until today
pediod = 86400 # pull daily data (86,400 seconds per day)

def get_crypto_data(poloniex_pair):
    '''Retrieve cryptocurrency data from poloniex'''
    json_url = base_polo_url.format(poloniex_pair, start_date.timestamp(), end_date.timestamp(), pediod)
    data_df = get_json_data(json_url, poloniex_pair)
    data_df = data_df.set_index('date')
    return data_df

In [0]:
altcoins = ['ETH','LTC','XRP','ETC','STR','DASH','SC','XMR','XEM','DGB','GRIN']

altcoin_data = {}
for altcoin in altcoins:
    coinpair = 'BTC_{}'.format(altcoin)
    crypto_price_df = get_crypto_data(coinpair)
    altcoin_data[altcoin] = crypto_price_df

Loaded https://poloniex.com/public?command=returnChartData&currencyPair=BTC_ETH&start=1420070400.0&end=1553994325.658267&period=86400 from cache
Loaded https://poloniex.com/public?command=returnChartData&currencyPair=BTC_LTC&start=1420070400.0&end=1553994325.658267&period=86400 from cache
Loaded https://poloniex.com/public?command=returnChartData&currencyPair=BTC_XRP&start=1420070400.0&end=1553994325.658267&period=86400 from cache
Loaded https://poloniex.com/public?command=returnChartData&currencyPair=BTC_ETC&start=1420070400.0&end=1553994325.658267&period=86400 from cache
Loaded https://poloniex.com/public?command=returnChartData&currencyPair=BTC_STR&start=1420070400.0&end=1553994325.658267&period=86400 from cache
Loaded https://poloniex.com/public?command=returnChartData&currencyPair=BTC_DASH&start=1420070400.0&end=1553994325.658267&period=86400 from cache
Loaded https://poloniex.com/public?command=returnChartData&currencyPair=BTC_SC&start=1420070400.0&end=1553994325.658267&period=86

#  9 AltCoins
- Dictionary with 9 dataframes, each containing the historical daily average exchange prices between the altcoin and Bitcoin.

- Preview the last few rows of the Ethereum price table to visually verify

In [0]:
altcoin_data['ETH'].tail()

close      high       low      open   quoteVolume      volume  \
date                                                                           
2019-03-27  0.034520  0.034634  0.033939  0.033939  16189.602720  556.220622   
2019-03-28  0.034251  0.034574  0.034100  0.034505   2798.628890   96.033657   
2019-03-29  0.034782  0.034782  0.034100  0.034251  11091.366981  384.390722   
2019-03-30  0.034667  0.035329  0.034448  0.034782   8292.517948  288.986455   
2019-03-31  0.034530  0.034697  0.034530  0.034670     87.976814    3.046740   

            weightedAverage  
date                         
2019-03-27         0.034357  
2019-03-28         0.034315  
2019-03-29         0.034657  
2019-03-30         0.034849  
2019-03-31         0.034631

# Convert Prices to USD
Since we now have the exchange rate for each cryptocurrency to Bitcoin, and we have the Bitcoin/USD historical pricing index, we can directly calculate the USD price series for each altcoin.

Here, we've created a new column in each altcoin dataframe with the USD prices for that coin.
Next, we can re-use our merge_dfs_on_column function from earlier to create a combined dataframe of the USD price for each cryptocurrency.

Now let's also add the Bitcoin prices as a final column to the combined dataframe.

In [0]:
# Calculate USD Price as a new column in each altcoin dataframe
for altcoin in altcoin_data.keys():
    altcoin_data[altcoin]['price_usd'] =  altcoin_data[altcoin]['weightedAverage'] * btc_usd_datasets['AVGBTCPRICEUSD']

In [0]:
# Merge USD price of each altcoin into single dataframe 
combined_df = merge_dfs_on_column(list(altcoin_data.values()), list(altcoin_data.keys()), 'price_usd')

In [0]:
# Add BTC price to the dataframe
combined_df['BTC'] = btc_usd_datasets['AVGBTCPRICEUSD']

In [0]:
# NOTE: need to call configure_plotly_browser_state() in every cell that we need to plot
configure_plotly_browser_state()
# Chart all of the altocoin prices
df_scatter(combined_df, 'Cryptocurrency Prices (USD)', seperate_y_axis=False, y_axis_label='Coin Value (USD)', scale='log')